In [1]:
import cv2 as cv
import numpy as np
from sklearn.cluster import DBSCAN
from sklearn import metrics
from matplotlib import pyplot as plt
import time
import sys
import multiprocessing
import os
import rospy
from sensor_msgs.msg import Image
from stereo_msgs.msg import DisparityImage
from sensor_msgs.msg import PointCloud2
from nav_msgs.msg import OccupancyGrid as Map
import message_filters
import cv_bridge
import tf
import math
from std_msgs.msg import String

In [2]:
def createLineIterator(P1, P2, img):
# """
# Produces and array that consists of the coordinates and intensities of
# each pixel in a line between two points

# Parameters:
#     -P1: a numpy array that consists of the coordinate of the first point (x,y)
#     -P2: a numpy array that consists of the coordinate of the second point (x,y)
#     -img: the image being processed

# Returns:
#     -it: a numpy array that consists of the coordinates and intensities of each
#     pixel in the radii (shape: [numPixels, 3], row = [x,y,intensity])     
# """
   #define local variables for readability
    #print img.shape
    image_height = img.shape[0]
    image_width = img.shape[1]
    P1X = P1[0]
    P1Y = P1[1]
    P2X = P2[0]
    P2Y = P2[1]
    
   #difference and absolute difference between points
   #used to calculate slope and relative location between points
    dX = P2X - P1X
    dY = P2Y - P1Y
    dXa = np.abs(dX)
    dYa = np.abs(dY)

    #predefine numpy array for output based on distance between points
    itbuffer = np.empty(shape=(np.maximum(dYa,dXa),3), dtype=np.int32)
    itbuffer.fill(np.nan)

   #Obtain coordinates along the line using a form of Bresenham's algorithm
    negY = P1Y > P2Y
    negX = P1X > P2X
    if P1X == P2X: #vertical line segment
        itbuffer[:,0] = P1X
        if negY:
            itbuffer[:,1] = np.arange(P1Y - 1,P1Y - dYa - 1,-1)
        else:
            itbuffer[:,1] = np.arange(P1Y+1,P1Y+dYa+1)              
    elif P1Y == P2Y: #horizontal line segment
        itbuffer[:,1] = P1Y
        if negX:
            itbuffer[:,0] = np.arange(P1X-1,P1X-dXa-1,-1)
        else:
            itbuffer[:,0] = np.arange(P1X+1,P1X+dXa+1)
    else: #diagonal line segment
        steepSlope = dYa > dXa
        if steepSlope:
            slope = dX.astype(np.float32)/dY.astype(np.float32)
            if negY:
                itbuffer[:,1] = np.arange(P1Y-1,P1Y-dYa-1,-1)
            else:
                itbuffer[:,1] = np.arange(P1Y+1,P1Y+dYa+1)
            itbuffer[:,0] = (slope*(itbuffer[:,1]-P1Y)).astype(np.int) + P1X
        else:
            slope = dY.astype(np.float32)/dX.astype(np.float32)
            if negX:
                itbuffer[:,0] = np.arange(P1X-1,P1X-dXa-1,-1)
            else:
                itbuffer[:,0] = np.arange(P1X+1,P1X+dXa+1)
            itbuffer[:,1] = (slope*(itbuffer[:,0]-P1X)).astype(np.int) + P1Y

   #Remove points outside of image
    colX = itbuffer[:,0]
    colY = itbuffer[:,1]
    itbuffer = itbuffer[(colX >= 0) & (colY >=0) & (colX<image_width) & (colY<image_height)]

   #Get intensities from img ndarray
    itbuffer[:,2] = img[itbuffer[:,1].astype(np.uint),itbuffer[:,0].astype(np.uint)]
    return itbuffer

In [3]:
# Initialization Stuff

rospy.init_node('liveproc')

listener = tf.TransformListener()
pub = rospy.Publisher('updated_map', Map, queue_size=10)

occ_map = None
up_occ_map = None
map_resolution = 0.5
origin = None
robot_x = 0
robot_y = 0
map_width = 0
map_height = 0
camera_range = 85/map_resolution
overlay = False
display_robot_yaw = False
display_rect = True
display_map = True
display_info = False

np.set_printoptions(threshold=sys.maxsize)

In [4]:
def rectangle(mat,color,image,original):
    
    global bearings
    global overlay
    global occ_map
    global tags
    global display_info
    
    rect = cv.boundingRect(mat)
    min_rect = cv.minAreaRect(mat)

    height = rect[3]
    width = rect[2]
    x = rect[0]
    x = np.int0(x)
    y = rect[1] 
    y = np.int0(y)
    font = cv.FONT_HERSHEY_SIMPLEX
    tag = 0
    if overlay:
        if (width < height and 4*width > height and width*height > 45):
            if(color =='green'):
                tag = 2
                cv.putText(original,color+' buoy',(np.int0(x-width/2),np.int0(y-height/2.5)), font, 0.5,(0,128,0),2,cv.LINE_AA)
                tags.append(tag)
            elif(color =='red'):
                tag = 3
                cv.putText(original,color+' buoy',(np.int0(x-width/2),np.int0(y-height/2.5)), font, 0.5,(0,0,128),2,cv.LINE_AA)
                tags.append(tag)
            else:
                tag = 1
                cv.putText(original,'buoy',(np.int0(x-width/2),np.int0(y-height/2.5)), font, 0.5,(255,255,255),2,cv.LINE_AA)
                tags.append(tag)
            cv.rectangle(original,(x,y),(x+width,y+height),(255,0,255),2)
            bearing = (min_rect[0][0]-640.0)/1280.0*80.0
            bearings.append(bearing)
            if display_info and occ_map.header.seq % 5 == 0:
                print bearings
                print tags
        if(tag == 0):
            image[y:y+height][x:x+width]=[0,0,0]
        return original
    else:
        if (width < height and 4*width > height and width*height > 45):
            if(color =='green'):
                tag = 2
                cv.putText(image,color+' buoy',(np.int0(x-width/2),np.int0(y-height/2.5)), font, 0.5,(255,255,255),2,cv.LINE_AA)
                tags.append(tag)
            elif(color =='red'):
                tag = 3
                cv.putText(image,color+' buoy',(np.int0(x-width/2),np.int0(y-height/2.5)), font, 0.5,(255,255,255),2,cv.LINE_AA)
                tags.append(tag)
            else:
                tag = 1
                cv.putText(image,'buoy',(np.int0(x-width/2),np.int0(y-height/2.5)), font, 0.5,(255,255,255),2,cv.LINE_AA)
                tags.append(tag)
            cv.rectangle(image,(x,y),(x+width,y+height),(255,0,255),2)
            bearing = (min_rect[0][0]-640.0)/1280.0*80.0
            bearings.append(bearing)
            if display_info and occ_map.header.seq % 5 == 0:
                print bearings
                print tags
        return image

In [5]:
def get_mapnbot_info(trans,robot_yaw):

    global map_resolution
    global robot_x
    global robot_y
    global map_width
    global map_height
    global origin
    global occ_map
    
    map_array = occ_map.data

    map_width = occ_map.info.width
    map_height = occ_map.info.height
    map_np = np.reshape(np.array(map_array),(map_height,map_width))
    robot_x = (trans[0]-origin.x)/map_resolution
    robot_y = (trans[1]-origin.y)/map_resolution
    robot_yaw = (90 - robot_yaw)
    while robot_yaw > 360:
        robot_yaw = robot_yaw - 360
    while robot_yaw < 0:
        robot_yaw = robot_yaw + 360
    
    return map_np, robot_yaw

In [6]:
def disp_rect(rect):
    cv.namedWindow("stereo/left/image_rect_color",cv.WINDOW_NORMAL)
    cv.imshow("stereo/left/image_rect_color", rect)
    cv.waitKey(1)

In [7]:
def map_filter(trans, robot_yaw):
    
    global origin
    global robot_x
    global robot_y
    global camera_range
    global occ_map
    global bearings
    global display_robot_yaw
    global tags
    
    map_np, robot_yaw = get_mapnbot_info(trans,robot_yaw) 
    
##############################################################################
# This is for visualization purposes.
# Set to false if you don't want to display the robot_yaw
# Delete it if it's irritating to look at
    if display_robot_yaw and occ_map.header.seq % 5 == 0:
        yaw_offset.append(0.0)
        print "Robot_yaw: ", robot_yaw
        print "Buoy yaw: ", buoy_yaw
        print len(slices)
##############################################################################
    
    slices = []
    i = 0
    while (i < len(bearings)):
        buoy_yaw = robot_yaw + bearings[i]
        if ((buoy_yaw) < 0):
            buoy_yaw = buoy_yaw + 360
        point_deltax = camera_range * math.sin(math.radians(buoy_yaw))
        point_deltay = camera_range * math.cos(math.radians(buoy_yaw))
        
        point1 = np.array([round(robot_x), round(robot_y)])
        point2 = np.array([round(robot_x+point_deltax), round(robot_y+point_deltay)])
        sliced = createLineIterator(point1.astype(int),point2.astype(int),map_np)
        slices.append(sliced)
###############################################################################################     

# If you uncomment the code below, make sure you change tags[i//1] to tags[i//3] in the draw_ray function

#         point3 = np.array([round(robot_x+1), round(robot_y)])
#         point4 = np.array([round(robot_x+point_deltax+1), round(robot_y+point_deltay)])
#         sliced = createLineIterator(point3.astype(int),point4.astype(int),map_np)
#         slices.append(sliced)
        
#         point5 = np.array([round(robot_x-1), round(robot_y)])
#         point6 = np.array([round(robot_x+point_deltax-1), round(robot_y+point_deltay)])
#         sliced = createLineIterator(point5.astype(int),point6.astype(int),map_np)
#         slices.append(sliced)
################################################################################################
        i+=1
    
    return slices

In [8]:
def draw_background_objects(map_img,map_np):
    
    global origin
    global robot_x
    global robot_y
    
    o_x = (-origin.x)/map_resolution
    o_y = (-origin.y)/map_resolution
# Color Assignment Section
    map_img[map_np == -1] = [255]    #Change to [255,255,255] for color
    map_img[map_np == 0] = [255]     #Change to [255,255,255] for color 
    map_img[map_np == 100] = [0]#Change to [0,0,0] for color
    origin_color = [0]#Change to [0,0,255] for color
    robot_color = [0]
# Origin (Drawn as a cross)

    map_img[int(o_y)+0][int(o_x)+0] = origin_color
    map_img[int(o_y)+0][int(o_x)+1] = origin_color
    map_img[int(o_y)+0][int(o_x)+2] = origin_color
    map_img[int(o_y)+1][int(o_x)+0] = origin_color
    map_img[int(o_y)+2][int(o_x)+0] = origin_color
    if (-origin.x) != 0:
        map_img[int(o_y)+0][int(o_x)-1] = origin_color
        map_img[int(o_y)+0][int(o_x)-2] = origin_color
    if (-origin.y) != 0:
        map_img[int(o_y)-1][int(o_x)+0] = origin_color
        map_img[int(o_y)-2][int(o_x)+0] = origin_color
# Robot (Drawn as a square)
    map_img[int(robot_y)+0][int(robot_x)+0] = robot_color
    map_img[int(robot_y)+0][int(robot_x)+2] = robot_color
    map_img[int(robot_y)+1][int(robot_x)+2] = robot_color
    map_img[int(robot_y)-1][int(robot_x)+2] = robot_color
    map_img[int(robot_y)+0][int(robot_x)-2] = robot_color
    map_img[int(robot_y)+1][int(robot_x)-2] = robot_color
    map_img[int(robot_y)-1][int(robot_x)-2] = robot_color
    map_img[int(robot_y)+2][int(robot_x)+0] = robot_color
    map_img[int(robot_y)+2][int(robot_x)+1] = robot_color
    map_img[int(robot_y)+2][int(robot_x)-1] = robot_color
    map_img[int(robot_y)-2][int(robot_x)+0] = robot_color
    map_img[int(robot_y)-2][int(robot_x)+1] = robot_color
    map_img[int(robot_y)-2][int(robot_x)-1] = robot_color
    
    return map_img

In [9]:
def draw_ray(map_img,slices):
    
    global display_robot_yaw
    global bearings
    global tags
    
    slices_size = len(slices)
    
    if not(display_robot_yaw):
        for i in range(int(slices_size)):
            try:
                found = False
                arr = slices[i]
                for ray in arr:
                    #print slice
                    if not found and (ray[2] == -1 or ray[2] == 0):
                        map_img[ray[1]][ray[0]] = [0]#Change to [255,0,0] for color
                    elif ray[2] == 100:
                        if tags[i//1] == 2: #here
                            map_img[ray[1]][ray[0]]=[180]#Change to [0,255,0] for color
                            found = True
                        if tags[i//1] == 3: #and here
                            map_img[ray[1]][ray[0]]=[230]#Change to [0,0,255] for color
                            found = True
            except Exception as ex:
                print ex
                print slices[i]
                print
    else:
        for arr in slices[-1]:
            map_img[arr[1]][arr[0]] = [0,255,0]
    return map_img

In [10]:
def get_map(slices):
    
    global camera_range
    global origin
    global robot_x
    global robot_y
    global map_width
    global map_height
    global occ_map
    
    map_np = np.reshape(np.array(occ_map.data),(map_height,map_width))

    map_img = np.zeros((map_height, map_width, 3))
    
    map_img = draw_background_objects(map_img,map_np)
    
    map_img = draw_ray(map_img,slices)
    
    map_img = np.swapaxes(map_img, 0, 1)
    
    return map_img

In [11]:
def disp_map(map_img):
    cv.namedWindow("map_inverted",cv.WINDOW_NORMAL)
    cv.imshow("map_inverted", map_img)
    cv.waitKey(1)

In [12]:
def transform(img):
    
    global bearings
    global tags
# Once a color image has been read, it passes through the 
# transform function. The transform function has two parts:
# pre-processing also known as pp which filters the image based
# of certain values in the hue, saturation, and value (hsv) 
# colorspace and the dbscan which clusters the processed image
# and classifies the clusters as either a buoy, a green buoy,
# a red buoy, or noise. No changes are needed.
    
    
    
    bridge = cv_bridge.CvBridge()
    
    bearings = []
    tags = []
    width = img.height
    height = img.width
    
    img = bridge.imgmsg_to_cv2(img, desired_encoding="passthrough")
    
    img = cv.cvtColor(img, cv.COLOR_RGB2BGR)  
    
    
    image = pp(img,width,height)
    
    img2= dbscan(image, img)
    
    return img2
def pp(image, width, height):
    
# The first function in transform is pp or preprocessing. The 
# first line truncates the lower half of the image. The reason
# this is because the plantoons from the wamv are always 
# blocking the camera vision and become noisy data. The
# function changes the image to the HSV colorspace and 
# filters out the image. No changes are needed. It returns 
# the filtered image in the BGR colorspace.The input is the
# color image.

    image = np.array(image[0:width][0:int(height*0.65)])
    image = cv.cvtColor(image, cv.COLOR_BGR2HSV)
    image[np.logical_not(np.logical_and(image[:,:,1] > 5,np.logical_or(np.logical_and(image[:,:,0] > 70, image[:,:,0] < 90),np.logical_or(image[:,:,0] >= 170, image[:,:,0] < 10))))] = [0,0,0]
    image = cv.cvtColor(image,cv.COLOR_HSV2BGR)

    return(image)
def dbscan(image, original):
    start_time_db = time.time()
# The second function in transform is dbscan. The inputs are 
# the filtered colored image and the original color image
# read from the imread statement. The output is the original
# image.This is the end of this classification algorithm.

###########################################################

# Part 1: Thresholding the image
##########################################################
# The reason we threshold the image before applying DBSCAN to 
# the points is because DBSCAN is a computational demanding 
# function. This part takes the filtered image, makes a 
# copy of it, and converts it into a grayscale image. The gray-
# scale image is thresholded at a value of 10. 0 is black and
# 255 is white. This takes the ~400,000 matrix points and 
# leaves only ~10,000 nonzero matrix points. 

    img = image.copy()
    img = cv.cvtColor(img, cv.COLOR_BGR2GRAY)

    ret,thresh1 = cv.threshold(img,10,255,cv.THRESH_BINARY)

# After thresholding the image, we pull out those nonzero
# points and assign it to the nonzero array variable. This
# array has dimensions of n rows and 2 columns. The first 
# column is the y coordinate and the second column is the x
# coordinate. These two arrays would be combined by 
# np.column_stack which merges the two arrays at their columns.

    nonzero = np.nonzero(thresh1)

    yp = np.array(nonzero[0])
    xp = np.array(nonzero[1])


    X=np.column_stack((xp,yp))
#########################################################

# Creating the BDSCAN object and Sorting Array with Labels
#########################################################    
# After thresholding the filtered image and creating an
# array of nonzero coordinates, this algorithm applies a
# clustering algorithm that filters the image based off the
# array X. If X is empty, this function ends and output is 
# the original input. The first line creates the DBSCAN
# object with an epsilon of 3 and minimum samples of 20. 
# Eps refers to the size of the neighborhood and the 
# min_samples refers to the minimum number of samples required
# for that neighborhood to be considered a cluster. The user
# is free to change the two values for eps and min_samples. The
# .fit(X) applies the matrix points to the DBSCAN object.
# One of the parameters of the db scan object are the labels.
# This is invoked by the line labels = db.labels. This creates
# an array of labels that assigns a number to the image index.
# n clusters have labels that start at 0 and end with n-1.For 
# example, if an image has four clusters, the labels would
# include 0,1,2, and 3. -1 is dedicated for noise. 

    if (len(X) > 0):
        start_time = time.time()
        db = DBSCAN(eps=3, min_samples=10).fit(X)
        labels = db.labels_
#         print (1.0*(time.time()-start_time))

# The array variable combines the x and y coordinates and the 
# labels in a single array aligned by column. The array is
# sorted with the sort variable with the values in the third
# column or the labels. For example, an image with four
# clusters and noise would be labeled in order from (-1,0,1,2,3).
# The while loop iterates from the beginning of the sorted loop
# and deletes every instance of -1 or until the list is empty.
# This while loop is needed because the noise data is
# irrelevant to the cluster algorithm and the user does not 
# know how much noise there is in the image. The image could 
# have no noise or it could all be noise. The output of this
# section is an array with coordinates sorted together in 
# clusters.

        array = zip(xp,yp,labels)
        sort = sorted(list(array), key=lambda x: x[2])

        x = 0
        while (len(sort) > 0 and sort[x][2] == -1):
            del sort[x]
#########################################################

# Iterating through and classifying each cluster
#########################################################
# After iterating through sort, the program is either left with
# an empty array or an array of coordinates sorted and grouped
# by each cluster. The user needs the number of clusters. The 
# next three lines in the big if block does this. unique_labels
# sorts the set of labels and removes -1 if present. The next 
# two lines creates a copy of the sort array and removes the 
# labels column from the array.

        if (len(sort) > 0):
            unique_labels = sorted(set(labels))
            if (unique_labels[0] == -1):
                unique_labels.remove(-1)
            points = sort
            points = np.delete(points,2,1)

# The program assigns three variables. The first one i iterates
# through sort and compare its label value to x for each 
# iteration until the very end of the sort array. The second
# x refers to the cluster that the program is currently class-
# ifying. It starts with 0 and continues classifying until it 
# has classified all clusters. The third variable is l and this
# array becomes all the points within a cluster. Every time the 
# variable i iterates through sort and is equal to the value of
# the current cluster x, the coordinates are appended to the 
# array l. Since this array is sorted, the first time the x 
# variable equals a different value- the cluster has been 
# accounted for. This array of l contains all the points within
# the cluster. This array and the filtered image gets passed
# through the color function. The result of the color function
# gets passed through the rectangle function with the array,
# filtered image, and original image. The x variable is 
# incremented for the next cluster and the l array is set equal 
# to zero. Once the while loop has iterated through all 
# clusters, the result of the rectangle function is set to the 
# original image and the original image is returned to the 
# transform function which is returned to the read function 
# which writes the image.

            i = 0
            x = 0
            l = []
            while (x < len(unique_labels)):
                if (i < len(sort) and sort[i][2] == x):
                    l.append(points[i])
                    i+=1
                else:
                    x+=1
                    time_color = time.time()
                    clr = color_hsv(np.array(l),image)
                    print "color ", time.time()-time_color
                    time_rect = time.time()
                    tb = rectangle(np.array(l),clr,image,original)
                    print "rect ", time.time()-time_rect
                    print ""
                    l = []
            original = tb
    print time.time()-start_time_db
    print ""
    return original
def color(mat,image):
    
    ############################################################

# For the color function, the points of the cluster and the 
# filtered image are passed through. In this function, the 
# average red, green, and blue pixel values are calculated
# from the image inside of the cluster. If the average value
# fits within a certain range, the string 'red' or 'green' is 
# returned. Otherwise, the function returns the string 'none'
# The user is free to change the range of the BGR values that
# determine whether the buoy is red or green.

    sumred = 0
    sumgrn = 0
    sumblu = 0
    for x in range(len(mat)):
        sumred += image [mat[x][1]] [mat[x][0]] [2]
        sumgrn += image [mat[x][1]] [mat[x][0]] [1]
        sumblu += image [mat[x][1]] [mat[x][0]] [0]
    if ((sumred/len(mat)) > 80 and (sumred/len(mat)) < 180 and (sumgrn/len(mat)) > 30 and (sumgrn/len(mat)) < 115  and (sumblu/len(mat)) > 30 and (sumblu/len(mat)) < 110):
        return 'red'
    if ((sumred/len(mat)) > 30 and (sumred/len(mat)) < 80 and (sumgrn/len(mat)) > 60 and (sumgrn/len(mat)) < 180  and (sumblu/len(mat)) > 50 and (sumblu/len(mat)) < 130):
        return 'green'
    else:
        return 'none'
def color_hsv(mat, image):
    
# The rectangle function's parameters are the array of coordinates
# of the cluster, the color of the cluster, the filtered image,
# and the original image. The boundingRect function applies
# a non-rotated rectangle to the image points and returns four
# values in an array, the x and y coordinates of the leftmost
# corner and the width and height. These values are converted
# to ints. The font is set to Hershey Simple for the text and
# the tag is set to zero. The tag is useful in the classifica-
# tion of the buoy. The first classification of the buoy is 
# the proportion of the width and height. If the height is
# between 1.5 times the width and 3.5 times the width, the
# cluster is considered a buoy. If the cluster is given a 
# 'red' or 'green' color, it would be classified as a 'red buoy'
# or 'green buoy' respectively. Otherwise, it would simply be
# classified as a buoy. If any of these three options occur, 
# the tag is set to 1. If the height is not in that range
# mentioned above and the color is 'none', the cluster is
# classified as noise. The last function rectangle makes a 
# rectangle over the original image. The original image is sent
# back to the DBSCAN function.


    image = cv.cvtColor(image, cv.COLOR_BGR2HSV)
    sumhue = 0
    sumsat = 0
    sumval = 0
    mat_add = 0
    for x in range(len(mat)):
        if(image [mat[x][1]] [mat[x][0]] [2] > 5):
            mat_add = mat_add+1
            sumval += image [mat[x][1]] [mat[x][0]] [2]
            sumsat += image [mat[x][1]] [mat[x][0]] [1]
            sumhue += image [mat[x][1]] [mat[x][0]] [0]
    if mat_add > 0:
        sat = sumsat/mat_add
        val = sumval/mat_add
        hue = sumhue/mat_add
        #return (hue, sat, val)
        if (sat > 5 and val > 5 and (hue < 60 or hue >= 170)):
            return 'red'
        if (sat > 5 and val > 5 and (70 < hue < 90)):
            return 'green'
        else:
            return (hue, sat, val)

    return None

In [13]:
def callback(rect):
    
    global occ_map
    global origin
    global bearings
    global listener 
    global display_rect
    global display_map
    global tags
    global up_occ_map
    global pub
    
    origin = occ_map.info.origin.position
    rect = transform(rect)
    
    if not rospy.is_shutdown():       
        try:
            now = rospy.Time.now()
            listener.waitForTransform("/odom", "/front_left_camera_link", now, rospy.Duration(0.5))
            (trans,rot) = listener.lookupTransform("/odom", "/front_left_camera_link", now)
            euler = tf.transformations.euler_from_quaternion(rot)
            pixel_lines = map_filter(trans, math.degrees(euler[2]))
            map_image = get_map(pixel_lines)
#             print(map_image)
#             up_occ_map.data = map_image
            pub.publish(up_occ_map)
            if display_rect == True:
                disp_rect(rect)
            if display_map == True:
                disp_map(map_image)
        except tf.LookupException as l:
            print l
        except tf.ConnectivityException as c:
            print c
        except tf.ExtrapolationException as e:
            print e
        except Exception as ex:
            print ex 

In [14]:
def map_callback(p_map):
    
    global occ_map
    global up_occ_map
    
    occ_map = p_map    
    up_occ_map = p_map

In [15]:
if __name__ == '__main__':
    proj_map = rospy.Subscriber("projected_map", Map, map_callback)
    rect = rospy.Subscriber("stereo/left/image_rect_color", Image, callback)
    rospy.spin()   

color  0.00175595283508
rect  0.0002601146698

color  0.00235605239868
rect  0.000230073928833

color  0.00128817558289
rect  8.39233398438e-05

color  0.00154209136963
rect  0.000306129455566

color  0.00165700912476
rect  0.000236988067627

color  0.00392699241638
rect  0.000481843948364

color  0.00486493110657
rect  0.000555992126465

color  0.00137090682983
rect  4.60147857666e-05

color  0.00134992599487
rect  5.60283660889e-05

color  0.00163507461548
rect  5.79357147217e-05

color  0.00127601623535
rect  0.000169992446899

color  0.00114512443542
rect  0.00014591217041

color  0.00129795074463
rect  0.000133991241455

color  0.0012309551239
rect  5.81741333008e-05

color  0.00124907493591
rect  0.000297069549561

color  0.00139403343201
rect  0.000184059143066

color  0.0013210773468
rect  6.69956207275e-05

color  0.00187706947327
rect  0.000249147415161

color  0.00131607055664
rect  0.000130891799927

color  0.00134801864624
rect  0.000159978866577

color  0.00126385688782
r

rect  0.0015709400177

color  0.00708389282227
rect  0.000813961029053

color  0.00151085853577
rect  0.000111818313599

color  0.00138592720032
rect  0.000149011611938

color  0.00155997276306
rect  0.0001380443573

color  0.00136280059814
rect  0.000172138214111

color  0.00145888328552
rect  0.000221014022827

color  0.00193095207214
rect  0.000265836715698

color  0.00133895874023
rect  0.000139951705933

color  0.00149297714233
rect  0.000170946121216

color  0.00112390518188
rect  0.000133037567139

color  0.00120997428894
rect  0.000386953353882

color  0.00150609016418
rect  0.000278949737549

color  0.00147914886475
rect  0.00037693977356

color  0.00157690048218
rect  0.00025200843811

color  0.00146389007568
rect  0.000146150588989

color  0.00127100944519
rect  0.000149011611938

color  0.00118589401245
rect  8.41617584229e-05

color  0.00196194648743
rect  0.000118970870972

color  0.00124907493591
rect  0.000131130218506

color  0.000974178314209
rect  0.000207901000977



color  0.00147891044617
rect  0.00021505355835

color  0.00209212303162
rect  0.000297069549561

color  0.00183701515198
rect  0.000544786453247

color  0.00153803825378
rect  0.00025200843811

color  0.00553703308105
rect  0.000530004501343

color  0.00537085533142
rect  0.0022759437561

color  0.00210690498352
rect  0.00031590461731

color  0.00119686126709
rect  7.60555267334e-05

color  0.0011568069458
rect  0.000131130218506

color  0.00148987770081
rect  0.000169992446899

color  0.00132608413696
rect  9.20295715332e-05

color  0.00180411338806
rect  0.000191926956177

color  0.00137090682983
rect  0.000133037567139

color  0.00129318237305
rect  0.000257968902588

color  0.00122594833374
rect  8.10623168945e-05

color  0.00136995315552
rect  0.000193119049072

color  0.00146198272705
rect  0.000232219696045

color  0.00134110450745
rect  0.000133037567139

color  0.00135493278503
rect  6.19888305664e-05

color  0.00160908699036
rect  6.31809234619e-05

color  0.00156402587891
re

color  0.00797009468079
rect  0.000581026077271

color  0.00145602226257
rect  3.60012054443e-05

color  0.00152492523193
rect  0.000120162963867

color  0.00113701820374
rect  0.000135898590088

color  0.00128984451294
rect  0.000135898590088

color  0.00135803222656
rect  0.000174999237061

color  0.00325989723206
rect  0.000176906585693

color  0.00157594680786
rect  4.29153442383e-05

color  0.00320601463318
rect  9.29832458496e-05

color  0.00138902664185
rect  0.0028178691864

color  0.00170111656189
rect  0.000283002853394

color  0.00345802307129
rect  7.5101852417e-05

color  0.00157690048218
rect  0.000138998031616

color  0.00142812728882
rect  0.000516891479492

color  0.00150609016418
rect  6.31809234619e-05

color  0.00152492523193
rect  7.9870223999e-05

color  0.00132083892822
rect  0.000132083892822

0.0751690864563

color  0.00142407417297
rect  0.000155925750732

color  0.00151705741882
rect  0.000123023986816

color  0.00172305107117
rect  0.000355005264282

color  

color  0.00127410888672
rect  0.000245094299316

color  0.00475406646729
rect  0.000216007232666

color  0.00189113616943
rect  0.000450134277344

color  0.00207018852234
rect  0.000333070755005

color  0.00403594970703
rect  0.000361919403076

color  0.00493311882019
rect  0.000586032867432

color  0.00138211250305
rect  6.103515625e-05

color  0.00147199630737
rect  7.9870223999e-05

color  0.00226807594299
rect  0.000119924545288

color  0.00193285942078
rect  0.0001540184021

color  0.00157189369202
rect  0.000174999237061

color  0.00404000282288
rect  0.000195980072021

color  0.00157403945923
rect  0.000110149383545

color  0.00144910812378
rect  7.79628753662e-05

color  0.00154089927673
rect  0.000417947769165

color  0.00178194046021
rect  0.000162839889526

color  0.00149917602539
rect  0.000147104263306

color  0.00110697746277
rect  3.38554382324e-05

color  0.00110602378845
rect  0.000186920166016

color  0.00138187408447
rect  0.000140905380249

color  0.00157594680786
r

...

color  0.00116014480591
rect  0.00019097328186

color  0.00182509422302
rect  6.19888305664e-05

color  0.00427794456482
rect  0.000406980514526

color  0.00162887573242
rect  0.000298023223877

color  0.00416278839111
rect  0.00033712387085

color  0.00119209289551
rect  0.000211000442505

color  0.00117516517639
rect  0.000169038772583

color  0.00186204910278
rect  0.000139951705933

color  0.00133514404297
rect  0.000152826309204

color  0.00135397911072
rect  0.00019907951355

color  0.00112390518188
rect  0.000176906585693

color  0.00115990638733
rect  2.50339508057e-05

color  0.00118398666382
rect  3.00407409668e-05

color  0.00130701065063
rect  0.000111103057861

color  0.00119686126709
rect  0.000132083892822

color  0.0014910697937
rect  0.00019907951355

color  0.00171208381653
rect  6.103515625e-05

0.0502090454102

color  0.00159597396851
rect  5.79357147217e-05

color  0.00164794921875
rect  0.000326871871948

color  0.00382518768311
rect  0.000344038009644

color  0.0

color  0.00576591491699
rect  0.000605821609497

color  0.00119686126709
rect  0.000135183334351

color  0.00152397155762
rect  0.000134944915771

color  0.00120091438293
rect  3.00407409668e-05

color  0.00121212005615
rect  0.000191926956177

color  0.00161409378052
rect  0.000125885009766

color  0.00203108787537
rect  0.000107049942017

color  0.0011100769043
rect  3.69548797607e-05

color  0.00130200386047
rect  7.91549682617e-05

color  0.00998187065125
rect  0.000188112258911

color  0.0016930103302
rect  0.000187158584595

color  0.00180315971375
rect  0.00011682510376

color  0.00148820877075
rect  0.000164031982422

color  0.00183892250061
rect  0.000138998031616

color  0.00148391723633
rect  8.60691070557e-05

color  0.00143098831177
rect  5.91278076172e-05

color  0.00118494033813
rect  0.000128030776978

color  0.00114488601685
rect  6.19888305664e-05

color  0.00169396400452
rect  3.88622283936e-05

color  0.00114607810974
rect  0.000134944915771

color  0.0015070438385


color  0.00180101394653
rect  0.000272989273071

color  0.00190496444702
rect  0.000213861465454

color  0.00343418121338
rect  0.000530004501343

color  0.00134205818176
rect  0.000220060348511

color  0.00402498245239
rect  0.000647068023682

color  0.00961780548096
rect  0.000257968902588

color  0.00201010704041
rect  0.000216960906982

color  0.00132513046265
rect  0.000151872634888

color  0.00135803222656
rect  8.70227813721e-05

color  0.001305103302
rect  0.000412940979004

color  0.00140714645386
rect  0.000203847885132

color  0.00156784057617
rect  0.000173091888428

color  0.00164604187012
rect  0.0001540184021

color  0.00121307373047
rect  7.48634338379e-05

color  0.00179314613342
rect  0.000164985656738

color  0.00183415412903
rect  0.000204801559448

color  0.00152516365051
rect  3.60012054443e-05

color  0.00171685218811
rect  0.000137090682983

color  0.00124096870422
rect  5.60283660889e-05

color  0.00136494636536
rect  0.000175952911377

color  0.00145101547241


color  0.00158596038818
rect  4.60147857666e-05

color  0.00158381462097
rect  6.48498535156e-05

color  0.0014910697937
rect  0.000366926193237

color  0.00347304344177
rect  5.41210174561e-05

color  0.00190186500549
rect  0.00011682510376

color  0.000996828079224
rect  0.000138998031616

color  0.00103402137756
rect  0.000283002853394

color  0.00262522697449
rect  0.000215768814087

color  0.0022120475769
rect  0.000112056732178

color  0.00388407707214
rect  7.5101852417e-05

color  0.00093412399292
rect  0.00012993812561

color  0.00112509727478
rect  5.41210174561e-05

color  0.00119996070862
rect  0.000226020812988

color  0.00109505653381
rect  0.000177145004272

color  0.00130891799927
rect  0.000195980072021

color  0.00158596038818
rect  3.69548797607e-05

color  0.00129795074463
rect  5.72204589844e-05

0.0812449455261

color  0.0011899471283
rect  0.000179052352905

color  0.00198483467102
rect  0.000195980072021

color  0.00439500808716
rect  0.000483989715576

color  0

rect  0.000897169113159

color  0.00596785545349
rect  0.00065803527832

color  0.001629114151
rect  9.3936920166e-05

color  0.00154209136963
rect  0.000185966491699

color  0.00170516967773
rect  8.9168548584e-05

color  0.00167894363403
rect  0.000166893005371

color  0.00147294998169
rect  9.70363616943e-05

color  0.00177717208862
rect  3.09944152832e-05

color  0.00152087211609
rect  0.0002601146698

color  0.0014660358429
rect  5.29289245605e-05

color  0.00145697593689
rect  0.000195980072021

color  0.00163912773132
rect  3.2901763916e-05

color  0.0015230178833
rect  0.000113010406494

color  0.00125002861023
rect  0.000168085098267

color  0.00144004821777
rect  0.000175952911377

color  0.00184011459351
rect  0.000164031982422

color  0.00153708457947
rect  0.000159025192261

color  0.00155806541443
rect  0.000362873077393

color  0.00211811065674
rect  0.00020694732666

0.0730309486389

color  0.00097918510437
rect  0.000138998031616

color  0.00267505645752
rect  0.000235